<h1 align=center><font size = 5>Proyecto Final Capstone - La Batalla de los Vecindarios</font></h1>

<h2>Tabla de Contenido</h2>

<div class="alert alert-block alert-info" style="margin-top: 20px">
<ol>
    <li><a href="#introduccion">Introducción</a></li>
    <li><a href="#problema">Problema Comercial</a></li>
    <li><a href="#datos">Datos</a></li>
    <li><a href="#metodologia">Metodologia</a></li>
    <li><a href="#analisis">Analisis</a></li>
</ol>
    
</div>
 
<hr>

<h2 id="introduccion">1. Introducción</h2>

Para este proyecto nos centraremos en analizar y visualizar, los barrios de la ciudad de **Medellin-Colombia**, para determinar cual lugar es mejor para abrir una **pizzeria**.

<h2 id="problema">2. Problema Comercial</h2>

Un amigo cercano desea abrir un local de comida, especificamente una pizzeria, pero no tiene idea de en que lugar seria mas propicio abrir este local, en este emprendimiento tiene puesto sus esfuerzos y ahorros, es de vital importancia escoger bien el lugar donde estará la pizzeria.
Con la ayuda de la ciencia de datos, podemos darle un panomara claro, de donde es factible abrir la pizzeria y donde no lo es.

<h2 id="datos">3. Datos</h2>

<h3 id="datos">3.1. Fuentes de Datos</h3>

Los datos que vamos a utilizar, provienen de varias fuentes, una de ella es la base de datos proporcionada por la alcaldia de **Medellin**, donde se encuentran todos los barrios de medellin, la comuna a la que pertenecen, (parecido a los distritos en otras ciudades) y si son urbanos o rurales. Estos datos pueden ser consultados en este enlace: <a href="https://geomedellin-m-medellin.opendata.arcgis.com/datasets/M-Medellin::barrio-vereda/explore?location=6.268900%2C-75.595550%2C12.00&showTable=true">FuenteDatos<a/>.

<p>Tenemos la opción de hacer web scraping, con el paquete <b>BeautifulSoup</b>, que utilizamos en los laboratorios anteriores, o tambien podemos descargar el archivo en formato <b>.csv</b>, directamente desde la pagina de la alcaldia de Medellin. y cargarlo a nuestro Notebook, con Pandas.
Escogeremos esta opción por simplicidad.</p>
<p>Utilizaremos la libreria <b>GeoPy</b>, para recuperar los datos Geoespaciales de cada uno de los barrios de la ciudad y los combinaremos en una sola tabla.</p>
<p>Ademas utilizaremos los datos de la Api <b>FourSquare</b>, para recuperar lugares y calificaciones, de los negocios similares, para los que deseamos predecir las mejores ubicaciones.</p>

<h3 id="datos">3.2. Data Cleaning</h3>

Como los Datos provienen de varias fuentes es posible, que halla datos faltantes o nulos, decidí eliminar estos datos de nuestro DataFrame principal, al igual que solo trabajaremos con los barrios que sean catalogados como **Urbanos**, y eliminaremos los que aparecen como rurales.

<h3 id="metodologia">4. Metodologia</h3>

Abordaremos el problema utilizando la tecnica de agrupamiento que ya conocemos, **k-means**. Este enfoque permitirá a la audiencia ver como los veciendarios se parecen en sus datos demograficos.

### Importar librerias

In [1]:
import numpy as np # librería para manejar datos vectorizados

import pandas as pd # librería para análisis de datos
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # librería para manejar archivos JSON 

import requests # librería para manejar solicitudes
from pandas.io.json import json_normalize # librería para convertir un archivo json en un dataframe pandas

# Matplotlib y módulos asociados para graficar
import matplotlib.cm as cm
import matplotlib.colors as colors

# importar k-means desde la fase de agrupación
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # librería para graficar mapas 

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


### Cargamos el conjunto de datos de los barrios de **Medellin**.

In [2]:
dfBarrios = pd.read_csv('C:/Users/andrey.zapata/Downloads/Barrio_Vereda.csv')
dfBarrios.head(5)

OBJECTID CODIGO              NOMBRE  SUBTIPO_BARRIOVEREDA  \
0      1112   0510       Tricentenario                     1   
1      1113   0208          Villa Niza                     1   
2      1114   1108            Laureles                     1   
3      1115   1303  Santa Rosa de Lima                     1   
4      1116   1206         Santa Lucía                     1   

  NOMBRE_COMUNA_CORREGIMIENTO      SHAPEAREA     SHAPELEN  
0                    Castilla  420637.970349  2897.304229  
1                  Santa Cruz  143215.327504  1697.303318  
2            Laureles Estadio  707014.821267  3847.112683  
3                  San Javier  139970.996369  2158.954261  
4                  La América  275913.740234  3048.703385

#### Eliminamos los barrios que estan catalogados como **Rurales** y los barrios que no tienen nombre, o GeoPy no puede encontrar su datos Geoespaciales

In [3]:
indexNames = dfBarrios[ (dfBarrios['SUBTIPO_BARRIOVEREDA'] == 2)
                | (dfBarrios['NOMBRE'] == "Hospital San Vicente de Paúl")
                | (dfBarrios['NOMBRE'] == "Área de Expansión El Noral")
                | (dfBarrios['NOMBRE'] == "Facultad de Minas")
                | (dfBarrios['NOMBRE'] == "Facultad Veterinaria y Zootecnia U.de.A.")
                | (dfBarrios['NOMBRE'] == "U.P.B")
                | (dfBarrios['NOMBRE'] == "El Nogal-Los Almendros")
                | (dfBarrios['NOMBRE'] == "Cementerio Universal")
                | (dfBarrios['NOMBRE'] == "Centro Administrativo")
                | (dfBarrios['NOMBRE'] == "Facultad de Minas U. Nacional")
                | (dfBarrios['NOMBRE'] == "Las Acacias")
                | (dfBarrios['NOMBRE'] == "Plaza de Ferias")
                | (dfBarrios['NOMBRE'] == "Terminal de Transporte")
                | (dfBarrios['NOMBRE'] == "Oleoducto")
                | (dfBarrios['NOMBRE'] == "San Isidro")
                | (dfBarrios['NOMBRE'] == "Naranjal")
                | (dfBarrios['NOMBRE'] == "La Palma")
                | (dfBarrios['NOMBRE'] == "Las Palmas")
                | (dfBarrios['NOMBRE'] == "El Salado")
                | (dfBarrios['NOMBRE'] == "Altavista")                     
                | (dfBarrios['NOMBRE'] == "Sin Nombre") ].index
dfBarrios.drop(indexNames , inplace=True)
dfBarrios.head(5)

OBJECTID CODIGO              NOMBRE  SUBTIPO_BARRIOVEREDA  \
0      1112   0510       Tricentenario                     1   
1      1113   0208          Villa Niza                     1   
2      1114   1108            Laureles                     1   
3      1115   1303  Santa Rosa de Lima                     1   
4      1116   1206         Santa Lucía                     1   

  NOMBRE_COMUNA_CORREGIMIENTO      SHAPEAREA     SHAPELEN  
0                    Castilla  420637.970349  2897.304229  
1                  Santa Cruz  143215.327504  1697.303318  
2            Laureles Estadio  707014.821267  3847.112683  
3                  San Javier  139970.996369  2158.954261  
4                  La América  275913.740234  3048.703385

#### Verificamos el numero de resgistros resultantes.

In [4]:
dfBarrios.shape

(251, 7)

#### Importamos libreria **GeoPy**, para obtener los datos geoespaciales de los barrios de la ciudad

In [5]:
from geopy.geocoders import Nominatim

In [6]:
address = 'Medellin, CO'

geolocator = Nominatim(user_agent="mde_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Medellin City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Medellin City are 6.2443382, -75.573553.


### Insertamos 2 columnas nuevas para la latitud y longitud

In [7]:
dfBarrios.insert(7, "lat", "")
dfBarrios.insert(8, "lng", "")
dfBarrios.head(5)

OBJECTID CODIGO              NOMBRE  SUBTIPO_BARRIOVEREDA  \
0      1112   0510       Tricentenario                     1   
1      1113   0208          Villa Niza                     1   
2      1114   1108            Laureles                     1   
3      1115   1303  Santa Rosa de Lima                     1   
4      1116   1206         Santa Lucía                     1   

  NOMBRE_COMUNA_CORREGIMIENTO      SHAPEAREA     SHAPELEN lat lng  
0                    Castilla  420637.970349  2897.304229          
1                  Santa Cruz  143215.327504  1697.303318          
2            Laureles Estadio  707014.821267  3847.112683          
3                  San Javier  139970.996369  2158.954261          
4                  La América  275913.740234  3048.703385

#### Construimos un ciclo para asignar a cada fila, de nuestro DataFrame, los datos de **latitud** y **longitud**, resultantes de la libreria GeoPy

In [8]:
address = 'Medellin,CO'

for i in dfBarrios.index:
    nomBarrio = dfBarrios.loc[i, 'NOMBRE']
    addressFull = nomBarrio + "," + address
    geolocator = Nominatim(user_agent="mde_explorer")
    location = geolocator.geocode(addressFull)
    #print(str(i) + dfBarrios.loc[i, 'NOMBRE'])
    if(location.latitude is not None and location.longitude is not None):
        latitude = location.latitude
        longitude = location.longitude
    else:
        print(dfBarrios.loc[i, 'NOMBRE'] + "Tiene datos geoespaciales nulos")
        latitude = "NoData"
        longitude = "NoData"
        
    
    dfBarrios.loc[i, 'lat']= latitude
    dfBarrios.loc[i, 'lng']= longitude

#### Reseteamos el index de nuestro dataFrame y descartamos las columnas innecesarias 

In [9]:
dfBarrios.reset_index(inplace=True)
dfBarrios.drop(['index'], axis=1, inplace=True)
dfBarrios.head(10)

OBJECTID CODIGO                    NOMBRE  SUBTIPO_BARRIOVEREDA  \
0      1112   0510             Tricentenario                     1   
1      1113   0208                Villa Niza                     1   
2      1114   1108                  Laureles                     1   
3      1115   1303        Santa Rosa de Lima                     1   
4      1116   1206               Santa Lucía                     1   
5      1117   1205               La Floresta                     1   
6      1118   1617              Las Mercedes                     1   
7      1119   1016                    Boston                     1   
8      1120   0725  Nueva Villa de La Iguaná                     1   
9      1121   0905      Alejandro Echavarría                     1   

  NOMBRE_COMUNA_CORREGIMIENTO      SHAPEAREA     SHAPELEN      lat      lng  
0                    Castilla  420637.970349  2897.304229  6.29107 -75.5663  
1                  Santa Cruz  143215.327504  1697.303318  6.29565 -75.5634  
2            Laureles Estadio  707014.821267  3847.112683    6.242 -75.5958  
3                  San Javier  139970.996369  2158.954261   6.2651 -75.6064  
4                  La América  275913.740234  3048.703385  6.25744 -75.6074  
5                  La América  422571.913797  2734.223663  6.25641 -75.6014  
6                       Belén  376395.954028  3346.632592  6.23573 -75.6094  
7               La Candelaria  535706.432626  3120.282724  6.24804 -75.5576  
8                     Robledo   65026.710827  1838.740592  6.25994 -75.5817  
9                Buenos Aires  365418.273130  3884.167537  6.23877 -75.5463

<h3 id="analisis">5. Analisis</h3>

#### inicializamos los parametros para generar el mapa de la ciudad

In [10]:
address = 'Medellin, CO'

geolocator = Nominatim(user_agent="mde_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Medellin City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Medellin City are 6.2443382, -75.573553.


#### Generemos el mapa con sus marcadores

In [11]:
# crear un mapa de Medellin utilizando los valores de latitud y longitud
map_medellin = folium.Map(location=[latitude, longitude], zoom_start=12)

# añadir marcadores al mapa
for lat, lng, comuna, barrio in zip(dfBarrios['lat'], dfBarrios['lng'], dfBarrios['NOMBRE_COMUNA_CORREGIMIENTO'], dfBarrios['NOMBRE']):
    label = '{}, {}'.format(barrio, comuna)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_medellin)  
    
map_medellin

#### inicializamos los argumentos que utilizaremos para la Api Foursquare

In [12]:
CLIENT_ID = '3KQ23TNDRE4U545FXH421FR5OEUAJ0UU4PKVNC4XNHRE3LKM' # su ID de Foursquare
CLIENT_SECRET = 'L1MSXE30SXDOQ4CNBTSMIRK2ZAXX5NZ1S3S2IRU1OTMMEBEA' # Secreto de Foursquare
VERSION = '20180605' # versión de la API de Foursquare
LIMIT = 100 # Un valor límite para la API de Foursquare

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3KQ23TNDRE4U545FXH421FR5OEUAJ0UU4PKVNC4XNHRE3LKM
CLIENT_SECRET:L1MSXE30SXDOQ4CNBTSMIRK2ZAXX5NZ1S3S2IRU1OTMMEBEA


#### Construimos una funcion para obtener los sitios cercanos de cada uno de los barrios de la ciudad.

In [13]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # crear la URL de solicitud de API
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # solicitud GET
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # regresa solo información relevante de cada sitio cercano
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

##### Llamamos la funcion que construimos

In [15]:
Medellin_venues = getNearbyVenues(names=dfBarrios['NOMBRE'],
                                   latitudes=dfBarrios['lat'],
                                   longitudes=dfBarrios['lng']
                                  )

Tricentenario
Villa Niza
Laureles
Santa Rosa de Lima
Santa Lucía
La Floresta
Las Mercedes
Boston
Nueva Villa de La Iguaná
Alejandro Echavarría
Picacho
Moscú No.2
Santo Domingo Savio No.1
El Danubio
La Avanzada
Perpetuo Socorro
San Lucas
Calasanz Parte Alta
Playón de Los Comuneros
El Chagualo
Cristo Rey
Los Conquistadores
Asomadera No.3
La Gloria
El Pesebre
Lalinde
Manrique Central No.1
Las Independencias
Parque Juan Pablo II
Moscú No.1
Bosques de San Pablo
Los Mangos
Los Cerros El Vergel
Miravalle
El Rodeo
La Milagrosa
El Castillo
San José La Cima No.1
El Raizal
Villa Guadalupe
El Poblado
Trinidad
El Pomar
Oriente
La Isla
La Sierra
María Cano-Carambolas
Belén
La Pilarica
El Corazón
Calle Nueva
La Frontera
Tejelo
Lorena
Miraflores
Los Ángeles
Alejandría
Metropolitano
La Francia
Cuarta Brigada
Los Naranjos
Aures No.1
Cataluña
Carpinelo
Andalucía
La Castellana
Carlos E. Restrepo
Robledo
Juan XXIII La Quiebra
Moravia
San Benito
Veinte de Julio
Altamira
Las Lomas No.2
Santander
Las Playas
S

#### Revisemos el tamaño del nuevo DataFrame y las primeras filas

In [16]:
print(Medellin_venues.shape)
Medellin_venues.head()

(2605, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Tricentenario                6.29107              -75.566325   
1  Tricentenario                6.29107              -75.566325   
2  Tricentenario                6.29107              -75.566325   
3  Tricentenario                6.29107              -75.566325   
4  Tricentenario                6.29107              -75.566325   

                            Venue  Venue Latitude  Venue Longitude  \
0  METRO - Estacion Tricentenario        6.290542       -75.564733   
1         Parque Juanes de la Paz        6.292663       -75.568673   
2         Club De Tenis El Bosque        6.293351       -75.568521   
3      Parche Tricen,Tienda mixta        6.292670       -75.564551   
4                   Indu Aires LS        6.288768       -75.567420   

               Venue Category  
0               Metro Station  
1           Recreation Center  
2                Tennis Court  
3               Grocery Store  
4  Construction & Landscaping

Revisemos cuantos retornaron para cada barrio

In [17]:
Medellin_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                
Aldea Pablo VI                                  2                       2   
Alejandro Echavarría                            5                       5   
Alejandría                                     16                      16   
Alfonso López                                   1                       1   
Altamira                                        3                       3   
Altos del Poblado                               4                       4   
Andalucía                                       5                       5   
Antonio Nariño                                  6                       6   
Aranjuez                                        4                       4   
Asomadera No.1                                  8                       8   
Asomadera No.2                                 32                      32   
Asomadera No.3                                  7                       7   
Astorga                                        97                      97   
Aures No.2                                      4                       4   
B. Cerro El Volador                             4                       4   
Barrio Caicedo                                  5                       5   
Barrio Colombia                                75                      75   
Barrio Colón                                   19                      19   
Barrio Cristóbal                                6                       6   
Barrios de Jesús                                1                       1   
Batallón Cuarta Brigada                        15                      15   
Batallón Girardot                               1                       1   
Belalcázar                                      3                       3   
Belencito                                       4                       4   
Bello Horizonte                                 1                       1   
Belén                                           1                       1   
Berlín                                          4                       4   
Bermejal-Los Álamos                             4                       4   
Betania                                         3                       3   
Bolivariana                                    30                      30   
Bomboná No.1                                   17                      17   
Bosques de San Pablo                            3                       3   
Boston                                         19                      19   
Boyacá                                          4                       4   
Brasilia                                        2                       2   
Buenos Aires                                    5                       5   
Calasanz                                       17                      17   
Calasanz Parte Alta                             1                       1   
Calle Nueva                                    19                      19   
Campo Alegre                                    4                       4   
Campo Amor                                     13                      13   
Campo Valdés No.1                               4                       4   
Campo Valdés No.2                               3                       3   
Caribe                                         15                      15   
Carlos E. Restrepo                             22                      22   
Carpinelo                                       2                       2   
Castilla                                       69                      69   
Castropol                                      26                      26   
Cataluña                                        4                       4   
Cerro Nutibara                                 24                      24   
Corazón de Jesús        

#### Encontremos cuantas categorías únicas se pueden conservar de todos los sitios regresados

In [18]:
print('Hay {} categorias unicas.'.format(len(Medellin_venues['Venue Category'].unique())))

Hay 241 categorias unicas.


### Analicemos cada barrio

In [19]:
# codificación
Medellin_onehot = pd.get_dummies(Medellin_venues[['Venue Category']], prefix="", prefix_sep="")

# añadir la columna de barrio de regreso al dataframe
Medellin_onehot['Neighbourhood'] = Medellin_venues['Neighborhood'] 

# mover la columna de barrio a la primer columna
fixed_columns = [Medellin_onehot.columns[-1]] + list(Medellin_onehot.columns[:-1])
Medellin_onehot = Medellin_onehot[fixed_columns]

Medellin_onehot.head()

Neighbourhood  Advertising Agency  Airport  Airport Service  \
0  Tricentenario                   0        0                0   
1  Tricentenario                   0        0                0   
2  Tricentenario                   0        0                0   
3  Tricentenario                   0        0                0   
4  Tricentenario                   0        0                0   

   Airport Terminal  American Restaurant  Amphitheater  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Asian Restaurant  Athletics & Sports  Auditorium  Auto Dealership  \
0                 0                   0           0                0   
1                 0                   0           0                0   
2                 0                   0           0                0   
3                 0                   0           0                0   
4                 0                   0           0                0   

   Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  Bakery  Bar  \
0            0              0                0          0       0    0   
1            0              0                0          0       0    0   
2            0              0                0          0       0    0   
3            0              0                0          0       0    0   
4            0              0                0          0       0    0   

   Baseball Field  Basketball Court  Bed & Breakfast  Beer Bar  Beer Garden  \
0               0                 0                0         0            0   
1               0                 0                0         0            0   
2               0                 0                0         0            0   
3               0                 0                0         0            0   
4               0                 0                0         0            0   

   Beer Store  Betting Shop  Big Box Store  Bike Rental / Bike Share  \
0           0             0              0                         0   
1           0             0              0                         0   
2           0             0              0                         0   
3           0             0              0                         0   
4           0             0              0                         0   

   Bike Trail  Bistro  Boarding House  Bookstore  Botanical Garden  \
0           0       0               0          0                 0   
1           0       0               0          0                 0   
2           0       0               0          0                 0   
3           0       0               0          0                 0   
4           0       0               0          0                 0   

   Bowling Alley  Brazilian Restaurant  Breakfast Spot  Brewery  Burger Joint  \
0              0                     0               0        0             0   
1              0                     0               0        0             0   
2              0                     0               0        0             0   
3              0                     0               0        0             0   
4              0                     0               0        0             0   

   Burrito Place  Bus Station  Bus Stop  Business Service  Cable Car  

Verifiquemos el nuevo tamaño del DataFrame

In [20]:
Medellin_onehot.shape

(2605, 242)

#### Agrupemos las filas por barrios tomando la média de la frecuencia de la ocurrencia de cada categoría

In [21]:
Medellin_grouped = Medellin_onehot.groupby('Neighbourhood').mean().reset_index()
Medellin_grouped

Neighbourhood  Advertising Agency   Airport  \
0                Aldea Pablo VI                0.00  0.000000   
1          Alejandro Echavarría                0.00  0.000000   
2                    Alejandría                0.00  0.000000   
3                 Alfonso López                0.00  0.000000   
4                      Altamira                0.00  0.000000   
5             Altos del Poblado                0.00  0.000000   
6                     Andalucía                0.00  0.000000   
7                Antonio Nariño                0.00  0.000000   
8                      Aranjuez                0.00  0.000000   
9                Asomadera No.1                0.00  0.000000   
10               Asomadera No.2                0.00  0.000000   
11               Asomadera No.3                0.00  0.000000   
12                      Astorga                0.00  0.000000   
13                   Aures No.2                0.00  0.000000   
14          B. Cerro El Volador                0.00  0.000000   
15               Barrio Caicedo                0.00  0.000000   
16              Barrio Colombia                0.00  0.000000   
17                 Barrio Colón                0.00  0.000000   
18             Barrio Cristóbal                0.00  0.000000   
19             Barrios de Jesús                0.00  0.000000   
20      Batallón Cuarta Brigada                0.00  0.000000   
21            Batallón Girardot                0.00  0.000000   
22                   Belalcázar                0.00  0.000000   
23                    Belencito                0.00  0.000000   
24              Bello Horizonte                0.00  0.000000   
25                        Belén                0.00  0.000000   
26                       Berlín                0.00  0.000000   
27          Bermejal-Los Álamos                0.00  0.000000   
28                      Betania                0.00  0.000000   
29                  Bolivariana                0.00  0.000000   
30                 Bomboná No.1                0.00  0.000000   
31         Bosques de San Pablo                0.00  0.000000   
32                       Boston                0.00  0.000000   
33                       Boyacá                0.00  0.000000   
34                     Brasilia                0.00  0.000000   
35                 Buenos Aires                0.00  0.000000   
36                     Calasanz                0.00  0.000000   
37          Calasanz Parte Alta                0.00  0.000000   
38                  Calle Nueva                0.00  0.000000   
39                 Campo Alegre                0.00  0.000000   
40                   Campo Amor                0.00  0.000000   
41            Campo Valdés No.1                0.00  0.000000   
42            Campo Valdés No.2                0.00  0.000000   
43                       Caribe                0.00  0.000000   
44           Carlos E. Restrepo                0.00  0.000000   
45                    Carpinelo                0.00  0.000000   
46                     Castilla                0.00  0.000000   
47                    Castropol                0.00  0.000000   
48                     Cataluña                0.00  0.000000   
49               Cerro Nutibara                0.00  0.000000   
50             Corazón de Jesús                0.00  0.000000   
51                   Cristo Rey                0.00  0.000000   
52               Cuarta Brigada                0.00  0.000000   
53                    Cucaracho                0.00  0.000000   
54                      Córdoba                0.00  0.000000   
55             Diego Echavarría                0.00  0.040000   
56         Doce de Octubre No.1                0.00  0.000000   
57         Doce de Octubre No.2                0.00  0.000000   
58   Ecoparque Cerro El Volador                0.00  0.000000   
59                  El Castillo                0.00  0.000000   
60                  El Chagualo                0.00  

Confirmemos el tamaño del DataFrame

In [22]:
Medellin_grouped.shape

(231, 242)

#### Imprimamos cada barrio junto con los 5 sitios mas comunes

In [23]:
num_top_venues = 5

for hood in Medellin_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = Medellin_grouped[Medellin_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Aldea Pablo VI----
                        venue  freq
0  Construction & Landscaping   0.5
1                  Restaurant   0.5
2          Advertising Agency   0.0
3                 Pastry Shop   0.0
4                Noodle House   0.0


----Alejandro Echavarría----
                venue  freq
0      Ice Cream Shop   0.2
1           Multiplex   0.2
2       Shopping Mall   0.2
3  Athletics & Sports   0.2
4        Tram Station   0.2


----Alejandría----
              venue  freq
0             Hotel  0.19
1     Shopping Mall  0.12
2         BBQ Joint  0.06
3       Coffee Shop  0.06
4  Sushi Restaurant  0.06


----Alfonso López----
                venue  freq
0   Electronics Store   1.0
1  Advertising Agency   0.0
2                Park   0.0
3           Nightclub   0.0
4        Noodle House   0.0


----Altamira----
                        venue  freq
0  Construction & Landscaping  0.33
1              Breakfast Spot  0.33
2                      Bakery  0.33
3          Advertising Agency 

#### pongamoslo en el DataFrame
Primero escribamos una función para ordenar los sitios en orden descendente.

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Generemos el nuevo dataframe y mostremos los primeros 10 sitios de cada barrio.

In [25]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# crear las columnas acorde al numero de sitios populares
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# crear un nuevo dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Medellin_grouped['Neighbourhood']

for ind in np.arange(Medellin_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Medellin_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood       1st Most Common Venue 2nd Most Common Venue  \
0        Aldea Pablo VI  Construction & Landscaping            Restaurant   
1  Alejandro Echavarría              Ice Cream Shop          Tram Station   
2            Alejandría                       Hotel         Shopping Mall   
3         Alfonso López           Electronics Store                   Zoo   
4              Altamira  Construction & Landscaping        Breakfast Spot   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Donut Shop          Food Service            Food Court   
1    Athletics & Sports         Shopping Mall             Multiplex   
2            Restaurant           Pizza Place    Frozen Yogurt Shop   
3        Ice Cream Shop          Food Service            Food Court   
4                Bakery         Event Service          Food Service   

      6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Food & Drink Shop                  Food     Fish & Chips Shop   
1         Food & Drink Shop                  Food     Fish & Chips Shop   
2  Mediterranean Restaurant      Sushi Restaurant                   Bar   
3         Food & Drink Shop                  Food     Fish & Chips Shop   
4                Food Court     Food & Drink Shop                  Food   

        9th Most Common Venue      10th Most Common Venue  
0  Financial or Legal Service        Fast Food Restaurant  
1  Financial or Legal Service               Event Service  
2                   BBQ Joint                        Café  
3  Financial or Legal Service        Fast Food Restaurant  
4           Fish & Chips Shop  Financial or Legal Service

### Agrupemos los barrios, **K-Means**
Ejecutemos _k_-means para agrupar los barrios en 5 agrupaciones.

In [26]:
# establecer el número de agrupaciones
kclusters = 5

Medellin_grouped_clustering = Medellin_grouped.drop('Neighbourhood', 1)

# ejecutar k-means
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Medellin_grouped_clustering)

# revisar las etiquetas de las agrupaciones generadas para cada fila del dataframe
kmeans.labels_[0:10]

array([0, 2, 2, 2, 2, 2, 3, 2, 2, 2])

Generemos un nuevo dataframe que incluya la agrupación asi como los 10 sitios mas populares de cada barrio.

In [28]:
# añadir etiquetas
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

Medellin_merged = dfBarrios

# juntar Medellin_grouped con dfBarrios
Medellin_merged = Medellin_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='NOMBRE')

Medellin_merged.head() # revisar las ultimas columnas

OBJECTID CODIGO              NOMBRE  SUBTIPO_BARRIOVEREDA  \
0      1112   0510       Tricentenario                     1   
1      1113   0208          Villa Niza                     1   
2      1114   1108            Laureles                     1   
3      1115   1303  Santa Rosa de Lima                     1   
4      1116   1206         Santa Lucía                     1   

  NOMBRE_COMUNA_CORREGIMIENTO      SHAPEAREA     SHAPELEN      lat      lng  \
0                    Castilla  420637.970349  2897.304229  6.29107 -75.5663   
1                  Santa Cruz  143215.327504  1697.303318  6.29565 -75.5634   
2            Laureles Estadio  707014.821267  3847.112683    6.242 -75.5958   
3                  San Javier  139970.996369  2158.954261   6.2651 -75.6064   
4                  La América  275913.740234  3048.703385  6.25744 -75.6074   

   Cluster Labels       1st Most Common Venue 2nd Most Common Venue  \
0             2.0  Construction & Landscaping         Grocery Store   
1             2.0               Grocery Store    Real Estate Office   
2             2.0                         Bar   Peruvian Restaurant   
3             NaN                         NaN                   NaN   
4             2.0            Business Service           Supermarket   

    3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0       Recreation Center          Tennis Court            Metro Station   
1  Furniture / Home Store                  Farm  Health & Beauty Service   
2             Pizza Place          Burger Joint       Italian Restaurant   
3                     NaN                   NaN                      NaN   
4            Soccer Field    Athletics & Sports            Metro Station   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Zoo                  Farm         Event Service   
1                   Zoo        Farmers Market         Event Service   
2  Gym / Fitness Center                Bakery                 Hotel   
3                   NaN                   NaN                   NaN   
4            Eye Doctor    Falafel Restaurant                  Farm   

  9th Most Common Venue 10th Most Common Venue  
0            Eye Doctor     Falafel Restaurant  
1            Eye Doctor     Falafel Restaurant  
2    Mexican Restaurant             Food Stand  
3                   NaN                    NaN  
4        Farmers Market                    Zoo

Antes de visualizar las agrupaciones, eliminemos algunas columnas innecesarias

In [29]:
Medellin_merged.drop(['OBJECTID', 'CODIGO', 'SUBTIPO_BARRIOVEREDA', 'SHAPEAREA', 'SHAPELEN' ], axis = 'columns', inplace=True)
Medellin_merged.head()

NOMBRE NOMBRE_COMUNA_CORREGIMIENTO      lat      lng  \
0       Tricentenario                    Castilla  6.29107 -75.5663   
1          Villa Niza                  Santa Cruz  6.29565 -75.5634   
2            Laureles            Laureles Estadio    6.242 -75.5958   
3  Santa Rosa de Lima                  San Javier   6.2651 -75.6064   
4         Santa Lucía                  La América  6.25744 -75.6074   

   Cluster Labels       1st Most Common Venue 2nd Most Common Venue  \
0             2.0  Construction & Landscaping         Grocery Store   
1             2.0               Grocery Store    Real Estate Office   
2             2.0                         Bar   Peruvian Restaurant   
3             NaN                         NaN                   NaN   
4             2.0            Business Service           Supermarket   

    3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0       Recreation Center          Tennis Court            Metro Station   
1  Furniture / Home Store                  Farm  Health & Beauty Service   
2             Pizza Place          Burger Joint       Italian Restaurant   
3                     NaN                   NaN                      NaN   
4            Soccer Field    Athletics & Sports            Metro Station   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Zoo                  Farm         Event Service   
1                   Zoo        Farmers Market         Event Service   
2  Gym / Fitness Center                Bakery                 Hotel   
3                   NaN                   NaN                   NaN   
4            Eye Doctor    Falafel Restaurant                  Farm   

  9th Most Common Venue 10th Most Common Venue  
0            Eye Doctor     Falafel Restaurant  
1            Eye Doctor     Falafel Restaurant  
2    Mexican Restaurant             Food Stand  
3                   NaN                    NaN  
4        Farmers Market                    Zoo

Tratamiento de datos: renombrar columnas con espacios, eliminar valores nulos, etc

In [36]:
Medellin_merged.rename(columns = {'Cluster Labels':'ClusterLabels'}, inplace = True)
Medellin_merged.ClusterLabels = Medellin_merged.ClusterLabels.fillna(9)
Medellin_merged.ClusterLabels = Medellin_merged.ClusterLabels.astype(int)
Medellin_merged.head(5)

NOMBRE NOMBRE_COMUNA_CORREGIMIENTO      lat      lng  \
0       Tricentenario                    Castilla  6.29107 -75.5663   
1          Villa Niza                  Santa Cruz  6.29565 -75.5634   
2            Laureles            Laureles Estadio    6.242 -75.5958   
3  Santa Rosa de Lima                  San Javier   6.2651 -75.6064   
4         Santa Lucía                  La América  6.25744 -75.6074   

   ClusterLabels       1st Most Common Venue 2nd Most Common Venue  \
0              2  Construction & Landscaping         Grocery Store   
1              2               Grocery Store    Real Estate Office   
2              2                         Bar   Peruvian Restaurant   
3              9                         NaN                   NaN   
4              2            Business Service           Supermarket   

    3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  \
0       Recreation Center          Tennis Court            Metro Station   
1  Furniture / Home Store                  Farm  Health & Beauty Service   
2             Pizza Place          Burger Joint       Italian Restaurant   
3                     NaN                   NaN                      NaN   
4            Soccer Field    Athletics & Sports            Metro Station   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Zoo                  Farm         Event Service   
1                   Zoo        Farmers Market         Event Service   
2  Gym / Fitness Center                Bakery                 Hotel   
3                   NaN                   NaN                   NaN   
4            Eye Doctor    Falafel Restaurant                  Farm   

  9th Most Common Venue 10th Most Common Venue  
0            Eye Doctor     Falafel Restaurant  
1            Eye Doctor     Falafel Restaurant  
2    Mexican Restaurant             Food Stand  
3                   NaN                    NaN  
4        Farmers Market                    Zoo

In [39]:
indexNames = Medellin_merged[ (Medellin_merged['ClusterLabels'] == 9)].index
Medellin_merged.drop(indexNames, inplace=True)
Medellin_merged.head(5)

NOMBRE NOMBRE_COMUNA_CORREGIMIENTO      lat      lng  ClusterLabels  \
0  Tricentenario                    Castilla  6.29107 -75.5663              2   
1     Villa Niza                  Santa Cruz  6.29565 -75.5634              2   
2       Laureles            Laureles Estadio    6.242 -75.5958              2   
4    Santa Lucía                  La América  6.25744 -75.6074              2   
5    La Floresta                  La América  6.25641 -75.6014              2   

        1st Most Common Venue 2nd Most Common Venue   3rd Most Common Venue  \
0  Construction & Landscaping         Grocery Store       Recreation Center   
1               Grocery Store    Real Estate Office  Furniture / Home Store   
2                         Bar   Peruvian Restaurant             Pizza Place   
4            Business Service           Supermarket            Soccer Field   
5               Metro Station          Burger Joint                   Hotel   

  4th Most Common Venue    5th Most Common Venue 6th Most Common Venue  \
0          Tennis Court            Metro Station                   Zoo   
1                  Farm  Health & Beauty Service                   Zoo   
2          Burger Joint       Italian Restaurant  Gym / Fitness Center   
4    Athletics & Sports            Metro Station            Eye Doctor   
5                  Park               Restaurant        Breakfast Spot   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0                  Farm         Event Service            Eye Doctor   
1        Farmers Market         Event Service            Eye Doctor   
2                Bakery                 Hotel    Mexican Restaurant   
4    Falafel Restaurant                  Farm        Farmers Market   
5           Supermarket                   Zoo    Falafel Restaurant   

  10th Most Common Venue  
0     Falafel Restaurant  
1     Falafel Restaurant  
2             Food Stand  
4                    Zoo  
5                   Farm

Despues de ajustar el formato de nuestros datos, procedemos a visualizar las agrupaciones resultantes

In [43]:
#crear mapa
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=13)

# establecer el esquema de color para las agrupaciones
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# añadir marcadores al mapa
markers_colors = []
for lat, lon, poi, cluster in zip(Medellin_merged['lat'], Medellin_merged['lng'], Medellin_merged['NOMBRE'], Medellin_merged['ClusterLabels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### Examinemos el resultados de las agrupaciones

**Agrupacion 1**

In [46]:
Medellin_merged.loc[Medellin_merged['ClusterLabels'] == 0, Medellin_merged.columns[[0] + list(range(5, Medellin_merged.shape[1]))]]

NOMBRE       1st Most Common Venue      2nd Most Common Venue  \
43          Oriente  Construction & Landscaping          French Restaurant   
63        Carpinelo  Construction & Landscaping                 Restaurant   
158        Brasilia                  Restaurant  Latin American Restaurant   
218  Aldea Pablo VI  Construction & Landscaping                 Restaurant   
225         Córdoba  Construction & Landscaping             Ice Cream Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
43         Cosmetics Shop              Creperie          Food Service   
63             Donut Shop          Food Service            Food Court   
158                   Zoo            Donut Shop            Food Court   
218            Donut Shop          Food Service            Food Court   
225          Food Service            Food Court     Food & Drink Shop   

    6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
43             Food Court     Food & Drink Shop                        Food   
63      Food & Drink Shop                  Food           Fish & Chips Shop   
158     Food & Drink Shop                  Food           Fish & Chips Shop   
218     Food & Drink Shop                  Food           Fish & Chips Shop   
225                  Food     Fish & Chips Shop  Financial or Legal Service   

          9th Most Common Venue      10th Most Common Venue  
43            Fish & Chips Shop  Financial or Legal Service  
63   Financial or Legal Service        Fast Food Restaurant  
158  Financial or Legal Service        Fast Food Restaurant  
218  Financial or Legal Service        Fast Food Restaurant  
225        Fast Food Restaurant              Farmers Market

**Agrupacion 2**

In [47]:
Medellin_merged.loc[Medellin_merged['ClusterLabels'] == 1, Medellin_merged.columns[[0] + list(range(5, Medellin_merged.shape[1]))]]

NOMBRE       1st Most Common Venue  \
11              Moscú No.2  Construction & Landscaping   
24              El Pesebre          Advertising Agency   
30    Bosques de San Pablo                 Pizza Place   
37   San José La Cima No.1                        Park   
39         Villa Guadalupe  Construction & Landscaping   
46   María Cano-Carambolas                        Park   
48             La Pilarica                        Park   
52                  Tejelo              Ice Cream Shop   
67                 Robledo                        Park   
79          Barrio Caicedo                      Museum   
89              San Germán                  Print Shop   
93                Girardot                        Park   
104  San José La Cima No.2  Construction & Landscaping   
109            El Salvador                        Park   
114             Belalcázar                        Park   
126            La Libertad         Fried Chicken Joint   
135             La Mansión                        Park   
138          Los Alcázares                        Park   
146            San Antonio                        Park   
162           Santa Mónica        Fast Food Restaurant   
190                 Gerona                        Park   
191         Santa Teresita                 Pizza Place   
203      Manrique Oriental                        Park   
217                 Boyacá              Ice Cream Shop   
219          Villa Hermosa     Comfort Food Restaurant   
222                Betania  Construction & Landscaping   
227              Florencia                  Food Truck   
237               La Salle  Construction & Landscaping   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
11            Rental Service                   Gym                  Park   
24      Gym / Fitness Center              Mountain                  Park   
30                    Bakery                  Park                   Zoo   
37                       Zoo     Electronics Store          Food Service   
39            Rental Service           Men's Store                  Park   
46             Grocery Store            Donut Shop            Food Court   
48                      Food             BBQ Joint         Grocery Store   
52              Burger Joint                  Park     Electronics Store   
67           Motorcycle Shop  Gym / Fitness Center            Donut Shop   
79   Comfort Food Restaurant            Food Court                  Park   
89                      Park         Grocery Store                 Hotel   
93                      Farm                   Gym          Tennis Court   
104                     Park     French Restaurant          Soccer Field   
109          Nature Preserve      Department Store                   Zoo   
114                     Farm         Grocery Store            Donut Shop   
126                     Park                   Zoo     Electronics Store   
135                      Zoo     Electronics Store          Food Service   
138   Argentinian Restaurant         Metro Station               Dog Run   
146      Fried Chicken Joint              Mountain            Campground   
162             Burger Joint             BBQ Joint                  Park   
190                    Plaza           Supermarket      Department Store   
191     Fast Food Restaurant             BBQ Joint                  Park   
203              Pizza Place                   Zoo            Donut Shop   
217             Burger Joint                   Bar                  Park   
219                      Bar                  Park                   Zoo   
222                     Park                Museum                Hostel   
227       Mexican Restaurant             BBQ Joint                  Park   
237             Betting Shop           Bus Station                  Park   

    5th Most Common Venue       6th Most Common Venue 7th Most Common Venue  \
11      Fish & Chips Shop  Financial or Legal Service

**Agrupacion 3**

In [48]:
Medellin_merged.loc[Medellin_merged['ClusterLabels'] == 2, Medellin_merged.columns[[0] + list(range(5, Medellin_merged.shape[1]))]]

NOMBRE       1st Most Common Venue  \
0                 Tricentenario  Construction & Landscaping   
1                    Villa Niza               Grocery Store   
2                      Laureles                         Bar   
4                   Santa Lucía            Business Service   
5                   La Floresta               Metro Station   
6                  Las Mercedes                 Pizza Place   
7                        Boston                 Pizza Place   
8      Nueva Villa de La Iguaná          Seafood Restaurant   
9          Alejandro Echavarría              Ice Cream Shop   
10                      Picacho        Colombian Restaurant   
12     Santo Domingo Savio No.1                         Bar   
13                   El Danubio           Convenience Store   
14                  La Avanzada                       Plaza   
15             Perpetuo Socorro   Latin American Restaurant   
16                    San Lucas               Deli / Bodega   
17          Calasanz Parte Alta                        Café   
19                  El Chagualo                Soccer Field   
20                   Cristo Rey                       Plaza   
21           Los Conquistadores                       Hotel   
22               Asomadera No.3                       Hotel   
23                    La Gloria                Burger Joint   
25                      Lalinde                   BBQ Joint   
26        Manrique Central No.1            Department Store   
27           Las Independencias              Ice Cream Shop   
28         Parque Juan Pablo II                        Food   
29                   Moscú No.1        Fast Food Restaurant   
31                   Los Mangos                Home Service   
32         Los Cerros El Vergel              Ice Cream Shop   
33                    Miravalle                         Bar   
34                     El Rodeo                       Plaza   
35                 La Milagrosa                       Plaza   
36                  El Castillo           French Restaurant   
38                    El Raizal                Dance Studio   
40                   El Poblado                        Café   
41                     Trinidad                   BBQ Joint   
42                     El Pomar              Ice Cream Shop   
44                      La Isla          Real Estate Office   
47                        Belén                         Pub   
49                   El Corazón                     Brewery   
50                  Calle Nueva                  Restaurant   
53                       Lorena                Burger Joint   
54                   Miraflores              Ice Cream Shop   
55                  Los Ángeles                   Speakeasy   
56                   Alejandría                       Hotel   
58                   La Francia               Metro Station   
59               Cuarta Brigada                         Gym   
60                 Los Naranjos              Clothing Store   
62                     Cataluña  Construction & Landscaping   
65                La Castellana                  Restaurant   
66           Carlos E. Restrepo                      Bakery   
69                      Moravia                 Bus Station   
70                   San Benito              Clothing Store   
71              Veinte de Julio              Ice Cream Shop   
72                     Altamira  Construction & Landscaping   
73               Las Lomas No.2                       Hotel   
74                    Santander                Soccer Field   
75                   Las Playas               Shopping Mall   
77               Las Esmeraldas                  Bike Trail   
78                   San Miguel                       Plaza   
80          B. Cerro El Volador           Electronics Store   
82                 Suramericana                   BBQ Joint   
83                    San Pedro              Ice Cream Shop   
85               Asomadera No.1            Business Serv

**Agrupacion 4**

In [49]:
Medellin_merged.loc[Medellin_merged['ClusterLabels'] == 3, Medellin_merged.columns[[0] + list(range(5, Medellin_merged.shape[1]))]]

NOMBRE 1st Most Common Venue 2nd Most Common Venue  \
45               La Sierra             Cable Car     Convenience Store   
64               Andalucía             Cable Car    Real Estate Office   
68   Juan XXIII La Quiebra             Cable Car     Convenience Store   
81         Santa Margarita             Cable Car          Home Service   
84            Villa Turbay             Cable Car            Campground   
141          Olaya Herrera             Cable Car     Convenience Store   

      3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
45             Food Service            Food Court     Food & Drink Shop   
64   Furniture / Home Store         Metro Station                   Zoo   
68             Food Service            Food Court     Food & Drink Shop   
81                      Zoo            Food Court     Food & Drink Shop   
84                      Zoo            Food Court     Food & Drink Shop   
141            Food Service            Food Court     Food & Drink Shop   

    6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
45                   Food     Fish & Chips Shop  Financial or Legal Service   
64      Food & Drink Shop                  Food           Fish & Chips Shop   
68                   Food     Fish & Chips Shop  Financial or Legal Service   
81                   Food     Fish & Chips Shop  Financial or Legal Service   
84                   Food     Fish & Chips Shop  Financial or Legal Service   
141                  Food     Fish & Chips Shop  Financial or Legal Service   

          9th Most Common Venue 10th Most Common Venue  
45         Fast Food Restaurant         Farmers Market  
64   Financial or Legal Service   Fast Food Restaurant  
68         Fast Food Restaurant         Farmers Market  
81         Fast Food Restaurant         Farmers Market  
84         Fast Food Restaurant         Farmers Market  
141        Fast Food Restaurant         Farmers Market

**Agrupacion 5**

In [50]:
Medellin_merged.loc[Medellin_merged['ClusterLabels'] == 4, Medellin_merged.columns[[0] + list(range(5, Medellin_merged.shape[1]))]]

NOMBRE 1st Most Common Venue 2nd Most Common Venue  \
168     Las Estancias            Shoe Store                   Zoo   
180  Barrios de Jesús            Shoe Store                   Zoo   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
168            Food Stand            Food Court     Food & Drink Shop   
180            Food Stand            Food Court     Food & Drink Shop   

    6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
168                  Food     Fish & Chips Shop  Financial or Legal Service   
180                  Food     Fish & Chips Shop  Financial or Legal Service   

    9th Most Common Venue 10th Most Common Venue  
168  Fast Food Restaurant         Farmers Market  
180  Fast Food Restaurant         Farmers Market

### Gracias!!